In [1]:
import requests
import json
import pandas as pd
import os
import datetime


url_parliaments = "https://www.abgeordnetenwatch.de/api/v2/parliaments"
url_parliament_periods = "https://www.abgeordnetenwatch.de/api/v2/parliament-periods"
url_politicians = "https://www.abgeordnetenwatch.de/api/v2/politicians"
url_candidacies_mandates = "https://www.abgeordnetenwatch.de/api/v2/candidacies-mandates"


def get_path():
    if os.path.isdir(os.path.join(os.getcwd(), "files")):
        save_path = os.path.join(os.getcwd(), "files")
    else:
        save_path = os.path.join(os.getcwd(), "AW_scraper","files")
    return save_path

def load_data(link, range_ = 50):
    x = 0
    json_list = list()
    if range_ == None:
        url_parliament_periods = link
        myResponse = requests.get(url_parliament_periods)
        print(x)
        jData = json.loads(myResponse.content)
        if x == 0: 
#            print(jData)
            json_list.append(jData)


    else:
        while x >= 0:
            url_parliament_periods = link+f"?page={x}&pager_limit=1000"
            #'f"?id[gte]={x}&id[lt]={x+range_}"

            myResponse = requests.get(url_parliament_periods)
            print(x)
            jData = json.loads(myResponse.content)
            if x == 0: 
    #            print(jData)
                json_list.append(jData)
                x += 1
            else:
                if not json_list[-1]["data"]:
                    z = x
                    x = -1                
                else:
                    x += 1
                    json_list.append(jData)
            if x>=15850:
                x=-1
#        print(f"loaded {50*z} lines")



    return json_list, jData



In [2]:
url_candidacies_mandates = f"https://www.abgeordnetenwatch.de/api/v2/candidacies-mandates"#?id[gte]={x}&id[lt]={x+50}"
json_list, jData = load_data(url_candidacies_mandates)


0
1
2
3
4


In [3]:
json_list

[{'meta': {'abgeordnetenwatch_api': {'version': '2.7',
    'changelog': 'https://www.abgeordnetenwatch.de/api/version-changelog/aktuell',
    'licence': 'CC0 1.0',
    'licence_link': 'https://creativecommons.org/publicdomain/zero/1.0/deed.de',
    'documentation': 'https://www.abgeordnetenwatch.de/api/entitaeten/candidacy-mandate'},
   'status': 'ok',
   'status_message': '',
   'result': {'count': 1000,
    'total': 2721,
    'page': '0',
    'results_per_page': 1000}},
  'data': [{'id': 63661,
    'entity_type': 'candidacy_mandate',
    'label': 'Dirk Beyer (Rheinland-Pfalz 2021 - 2026)',
    'api_url': 'https://www.abgeordnetenwatch.de/api/v2/candidacies-mandates/63661',
    'id_external_administration': None,
    'id_external_administration_description': None,
    'type': 'mandate',
    'parliament_period': {'id': 127,
     'entity_type': 'parliament_period',
     'label': 'Rheinland-Pfalz 2021 - 2026',
     'api_url': 'https://www.abgeordnetenwatch.de/api/v2/parliament-periods/12

In [4]:

rows = list()
max_len_fractions=1

for i in json_list:
    candidacies_mandates_df = pd.DataFrame()
    counter = 0
    for key, value in i.items():
        if key == "data":
            for element in value:
                current_element=element.copy()
                if counter == 0:
                    print(element)
                    first_element = element.copy()

                if 'fraction_membership' in current_element:
                    fraction_list = [current_element['fraction_membership'][u]['label'] for u,v, in enumerate(current_element['fraction_membership']) ]
                    if len(fraction_list) > max_len_fractions:
                        max_len_fractions = len(fraction_list)
                    fraction_list = fraction_list + [None for z in range(max_len_fractions-len(fraction_list))]
                    fraction_dict = {"fraction_membership"+str(l+1):v for l,v in enumerate(fraction_list)}
                    current_element.pop('fraction_membership')
                else:
                    fraction_dict = {"fraction_membership"+str(u+1):None for u in range(max_len_fractions)}

                if current_element['parliament_period']['label'] != None:
                    parliamend_period_dict = {"parliament_period": current_element['parliament_period']["label"]}
                else:
                    parliamend_period_dict = {"parliamend_period": None}
                current_element.pop('parliament_period')

                if current_element['electoral_data'] != None:
                    if current_element['electoral_data']['electoral_list'] != None:
                        electoral_list_dict = {'electoral_list':current_element['electoral_data']['electoral_list']['label']}
                    else:
                        electoral_list_dict = {'electoral_list':None}
                    if current_element['electoral_data']['constituency'] != None:
                        constituency_dict = {'constituency':current_element['electoral_data']['constituency']['label']}
                    else:
                        constituency_dict = {'constituency':None}
                current_element.pop('electoral_data')

                if current_element["politician"] != None:
                    # current_element = current_element | {'politician': current_element['politician']['label'] }
                    politician_dict =  {'politician': current_element['politician']['label'] }
                else:
                    politician_dict =  {'politician': None}
                current_element.pop('politician')

                rows.append(current_element | fraction_dict | politician_dict | electoral_list_dict | constituency_dict | parliamend_period_dict | fraction_dict)

                counter += 1

save_path = "files"
#final_df.to_excel(os.path.join(save_path,"candidacies_mandate.xlsx"))
print(f"candidacies mandates end: {datetime.datetime.now()} \n")
print(f"max_len_fractions: {max_len_fractions}")
candidacies_mandates_df = pd.DataFrame(rows)
candidacies_mandates_df.to_excel("files\\candidacies_mandates.xlsx", index=False)

{'id': 63661, 'entity_type': 'candidacy_mandate', 'label': 'Dirk Beyer (Rheinland-Pfalz 2021 - 2026)', 'api_url': 'https://www.abgeordnetenwatch.de/api/v2/candidacies-mandates/63661', 'id_external_administration': None, 'id_external_administration_description': None, 'type': 'mandate', 'parliament_period': {'id': 127, 'entity_type': 'parliament_period', 'label': 'Rheinland-Pfalz 2021 - 2026', 'api_url': 'https://www.abgeordnetenwatch.de/api/v2/parliament-periods/127', 'abgeordnetenwatch_url': 'https://www.abgeordnetenwatch.de/rheinland-pfalz'}, 'politician': {'id': 182364, 'entity_type': 'politician', 'label': 'Dirk Beyer', 'api_url': 'https://www.abgeordnetenwatch.de/api/v2/politicians/182364', 'abgeordnetenwatch_url': 'https://www.abgeordnetenwatch.de/profile/dirk-beyer'}, 'start_date': '2025-01-01', 'end_date': None, 'info': 'Dirk Beyer ist am 01.01.2025 für Jens Guth in den Landtag von Rheinland-Pfalz nachgerückt.', 'electoral_data': {'id': 64536, 'entity_type': 'electoral_data', '

In [15]:
candidacies_mandates_df = pd.DataFrame(rows)
candidacies_mandates_df.to_excel("files\\candidacies_mandates.xlsx")